# Machine Translation using OpenNMT

# Jamo and Char Tokenization

In [1]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [3]:
!pip install hgtk

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
  Created wheel for hgtk: filename=hgtk-0.1.3-py2.py3-none-any.whl size=6689 sha256=c79e1449aa15b61035cead5f6ce27dcce6f4dc168f720c8444872605bbc5f22e
  Stored in directory: /home/ubuntu/.cache/pip/wheels/96/10/4b/0887dcaf5e0b0d26b807fef3497703fea2c44a76f91d198bd3
Successfully built hgtk


In [2]:
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src.code -s 32000

In [4]:
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-morph.txt

In [3]:
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-bpe.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [4]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-char.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-char.txt -save_data OpenNMT-py/Data/bpe2char/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-10 00:14:22,640 INFO] Extracting features...
[2020-12-10 00:14:22,641 INFO]  * number of source features: 0.
[2020-12-10 00:14:22,641 INFO]  * number of target features: 0.
[2020-12-10 00:14:22,641 INFO] Building `Fields` object...
[2020-12-10 00:14:22,641 INFO] Building & saving training data...
[2020-12-10 00:14:27,360 INFO] Building shard 0.
[2020-12-10 00:15:16,658 INFO]  * saving 0th train data shard to OpenNMT-py/Data/bpe2char/demo.train.0.pt.
[2020-12-10 00:15:17,676 INFO]  * tgt vocab size: 59.
[2020-12-10 00:15:17,697 INFO]  * src vocab size: 13999.
[2020-12-10 00:15:17,735 INFO] Building & saving validation data...
[2020-12-10 00:15:17,826 INFO] Building shard 0.
[2020-12-10 00:15:18,135 INFO]  * saving 0th valid data shard to OpenNMT-py/Data/bpe2char/demo.valid.0.pt.


!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [5]:
!nvidia-smi

Thu Dec 10 00:15:19 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   25C    P8    12W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [6]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/bpe2char/demo -save_model OpenNMT-py/Data/bpe2char/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 10000 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/bpe2char'

[2020-12-10 00:15:20,530 INFO]  * src vocab size = 13999
[2020-12-10 00:15:20,530 INFO]  * tgt vocab size = 59
[2020-12-10 00:15:20,530 INFO] Building model...
[2020-12-10 00:15:26,446 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(13999, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_feature

[2020-12-10 00:15:26,525 INFO] Starting training on GPU: [0]
[2020-12-10 00:15:26,525 INFO] Start training loop and validate every 1000 steps...
[2020-12-10 00:15:26,526 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:15:26,723 INFO] number of examples: 7305
[2020-12-10 00:15:39,062 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:15:39,219 INFO] number of examples: 7305
[2020-12-10 00:15:41,546 INFO] Step 50/50000; acc:   8.25; ppl: 26.99; xent: 3.30; lr: 0.00001; 5482/25759 tok/s;     15 sec
[2020-12-10 00:15:51,725 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:15:51,929 INFO] number of examples: 7305
[2020-12-10 00:15:56,206 INFO] Step 100/50000; acc:  17.59; ppl: 12.41; xent: 2.52; lr: 0.00001; 5724/26678 tok/s;     30 sec
[2020-12-10 00:16:03,961 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:16:04,172 INFO] number of examples: 7305
[2020-12

[2020-12-10 00:22:21,440 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:22:21,602 INFO] number of examples: 7305
[2020-12-10 00:22:31,222 INFO] Step 1350/50000; acc:  54.08; ppl:  3.54; xent: 1.26; lr: 0.00017; 5638/26482 tok/s;    425 sec
[2020-12-10 00:22:34,195 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:22:34,448 INFO] number of examples: 7305
[2020-12-10 00:22:46,118 INFO] Step 1400/50000; acc:  54.14; ppl:  3.53; xent: 1.26; lr: 0.00017; 5698/26255 tok/s;    440 sec
[2020-12-10 00:22:46,709 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:22:46,866 INFO] number of examples: 7305
[2020-12-10 00:22:59,424 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:22:59,665 INFO] number of examples: 7305
[2020-12-10 00:23:01,166 INFO] Step 1450/50000; acc:  55.08; ppl:  3.43; xent: 1.23; lr: 0.00018; 5537/25806 tok/s;    455 sec
[2020-12-10 00:23:12,06

[2020-12-10 00:29:21,246 INFO] number of examples: 7305
[2020-12-10 00:29:25,787 INFO] Step 2650/50000; acc:  70.76; ppl:  2.24; xent: 0.80; lr: 0.00033; 5503/25645 tok/s;    839 sec
[2020-12-10 00:29:33,792 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:29:33,954 INFO] number of examples: 7305
[2020-12-10 00:29:40,749 INFO] Step 2700/50000; acc:  71.17; ppl:  2.22; xent: 0.80; lr: 0.00033; 5630/26163 tok/s;    854 sec
[2020-12-10 00:29:46,647 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:29:46,916 INFO] number of examples: 7305
[2020-12-10 00:29:55,842 INFO] Step 2750/50000; acc:  71.58; ppl:  2.19; xent: 0.78; lr: 0.00034; 5547/25893 tok/s;    869 sec
[2020-12-10 00:29:59,466 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:29:59,626 INFO] number of examples: 7305
[2020-12-10 00:30:10,916 INFO] Step 2800/50000; acc:  71.92; ppl:  2.17; xent: 0.77; lr: 0.00035; 5579/25986 tok/s; 

[2020-12-10 00:36:20,443 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:36:20,712 INFO] number of examples: 7305
[2020-12-10 00:36:33,207 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:36:33,471 INFO] number of examples: 7305
[2020-12-10 00:36:34,982 INFO] Step 4000/50000; acc:  86.29; ppl:  1.51; xent: 0.42; lr: 0.00049; 5507/25665 tok/s;   1268 sec
[2020-12-10 00:36:34,984 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.valid.0.pt
[2020-12-10 00:36:35,502 INFO] number of examples: 8014
[2020-12-10 00:36:59,102 INFO] Validation perplexity: 54.8413
[2020-12-10 00:36:59,102 INFO] Validation accuracy: 24.7062
[2020-12-10 00:37:09,833 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 00:37:10,095 INFO] number of examples: 7305
[2020-12-10 00:37:13,929 INFO] Step 4050/50000; acc:  86.82; ppl:  1.49; xent: 0.40; lr: 0.00050; 2123/9957 tok/s;   1307 sec
[2020-12-10 00:37:22,626 INFO

...

[2020-12-10 04:14:15,682 INFO] number of examples: 7305
[2020-12-10 04:14:28,269 INFO] Step 44200/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00042; 5712/26264 tok/s;  14342 sec
[2020-12-10 04:14:28,270 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:14:28,544 INFO] number of examples: 7305
[2020-12-10 04:14:40,824 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:14:40,986 INFO] number of examples: 7305
[2020-12-10 04:14:43,321 INFO] Step 44250/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00042; 5471/25707 tok/s;  14357 sec
[2020-12-10 04:14:53,552 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:14:53,816 INFO] number of examples: 7305
[2020-12-10 04:14:58,208 INFO] Step 44300/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00042; 5637/26270 tok/s;  14372 sec
[2020-12-10 04:15:06,100 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:15:06

[2020-12-10 04:21:18,810 INFO] number of examples: 7305
[2020-12-10 04:21:26,284 INFO] Step 45500/50000; acc:  99.91; ppl:  1.00; xent: 0.00; lr: 0.00041; 5520/25513 tok/s;  14760 sec
[2020-12-10 04:21:31,288 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:21:31,450 INFO] number of examples: 7305
[2020-12-10 04:21:41,262 INFO] Step 45550/50000; acc:  99.93; ppl:  1.00; xent: 0.00; lr: 0.00041; 5557/26100 tok/s;  14775 sec
[2020-12-10 04:21:44,278 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:21:44,553 INFO] number of examples: 7305
[2020-12-10 04:21:56,504 INFO] Step 45600/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00041; 5569/25658 tok/s;  14790 sec
[2020-12-10 04:21:57,112 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:21:57,272 INFO] number of examples: 7305
[2020-12-10 04:22:09,879 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:22:10

[2020-12-10 04:28:23,866 INFO] number of examples: 7305
[2020-12-10 04:28:26,237 INFO] Step 46800/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00041; 5356/25168 tok/s;  15180 sec
[2020-12-10 04:28:36,642 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:28:36,805 INFO] number of examples: 7305
[2020-12-10 04:28:41,390 INFO] Step 46850/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00041; 5538/25812 tok/s;  15195 sec
[2020-12-10 04:28:49,293 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:28:49,456 INFO] number of examples: 7305
[2020-12-10 04:28:56,348 INFO] Step 46900/50000; acc:  99.93; ppl:  1.00; xent: 0.00; lr: 0.00041; 5632/26170 tok/s;  15210 sec
[2020-12-10 04:29:02,243 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:29:02,522 INFO] number of examples: 7305
[2020-12-10 04:29:11,350 INFO] Step 46950/50000; acc:  99.91; ppl:  1.00; xent: 0.00; lr: 0.00041; 5581/26048 tok

[2020-12-10 04:35:41,757 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:35:41,921 INFO] number of examples: 7305
[2020-12-10 04:35:51,676 INFO] Step 48100/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00040; 5388/25309 tok/s;  15625 sec
[2020-12-10 04:35:54,632 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:35:54,905 INFO] number of examples: 7305
[2020-12-10 04:36:06,802 INFO] Step 48150/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00040; 5611/25855 tok/s;  15640 sec
[2020-12-10 04:36:07,400 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:36:07,563 INFO] number of examples: 7305
[2020-12-10 04:36:20,402 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:36:20,677 INFO] number of examples: 7305
[2020-12-10 04:36:22,222 INFO] Step 48200/50000; acc:  99.92; ppl:  1.00; xent: 0.00; lr: 0.00040; 5404/25185 tok/s;  15656 sec
[2020-12-10 04:36:33

[2020-12-10 04:42:43,334 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:42:43,627 INFO] number of examples: 7305
[2020-12-10 04:42:48,083 INFO] Step 49400/50000; acc:  99.93; ppl:  1.00; xent: 0.00; lr: 0.00040; 5535/25798 tok/s;  16042 sec
[2020-12-10 04:42:56,247 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:42:56,410 INFO] number of examples: 7305
[2020-12-10 04:43:03,356 INFO] Step 49450/50000; acc:  99.93; ppl:  1.00; xent: 0.00; lr: 0.00040; 5515/25630 tok/s;  16057 sec
[2020-12-10 04:43:09,338 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:43:09,612 INFO] number of examples: 7305
[2020-12-10 04:43:18,394 INFO] Step 49500/50000; acc:  99.93; ppl:  1.00; xent: 0.00; lr: 0.00040; 5567/25987 tok/s;  16072 sec
[2020-12-10 04:43:21,895 INFO] Loading dataset from OpenNMT-py/Data/bpe2char/demo.train.0.pt
[2020-12-10 04:43:22,058 INFO] number of examples: 7305
[2020-12-10 04:43:33

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [16]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/bpe2char/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-bpe.txt -output OpenNMT-py/Data/bpe2char/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 17:56:48,278 INFO] Translating shard 0.
[2020-12-11 17:56:49,044 INFO] 
SENT 1: ['"@@', '경찰의', '설명을', '보면,', '손님@@', '으로', '피@@', '시@@', '방을', '찾은', '김씨는', '다른', '손님이', '남긴', '음식@@', '물을', '자리에서', '치@@', '워@@', '달라는', '요구를', '하다', '신@@', '씨와', '말@@', '다툼을', '했다고', '한다."']
PRED 1: s o m e ᴥ p a r t i c i p a t e ᴥ t h a t ᴥ s e n s e ᴥ w o r k ᴥ i s ᴥ a l o n e .
PRED SCORE: -0.0809

[2020-12-11 17:56:49,044 INFO] 
SENT 2: ['잠실@@', '여자@@', '고등학교@@', '(@@', '교장', '김인@@', '봉@@', ')는', '실@@', '력과', '인@@', '성을', '갖춘', '인재를', '기@@', '른@@', '다는', '지향@@', '점을', '가지고', '교사와', '학생이', '‘@@', '신뢰@@', '의', '팀@@', '플레이@@', '’를', '통해', '진로@@', '진학', '프로그램을', '업그레이드@@', '해', '나가고', '있다.']
PRED 2: " i n ᴥ a d d i t i o n , ᴥ n o ᴥ s e o u l ᴥ w a s ᴥ m o r e ᴥ p e o p l e ᴥ l i k e ᴥ t h i s . "
PRED SCORE: -0.0803

[2020-12-11 17:56:49,044 INFO] 
SENT 3: ['김', '전', '의원은', '이대로', '벌금', '100만', '원', '이상의', '형이', '확정되면', '5년', '동안', '선거@@', '권과', '피@@', '선거@@', '권을', '모두', '잃게', '된다.']
PRED 3

[2020-12-11 17:56:49,640 INFO] 
SENT 31: ['"@@', '단독', '콘서트', '무대가', '아닌,', '주', '시청@@', '층이', '청소년@@', '들인', '시상식', '무대@@', '였다는', '점에서', '화@@', '사의', '의@@', '상', '선택@@', '에는', '아쉬움이', '남@@', '는다."']
PRED 31: " a f t e r ᴥ c o m p a n i e s , ᴥ a n d ᴥ s e e m s ᴥ t o ᴥ b e ᴥ i n ᴥ o n e ᴥ p u r . "
PRED SCORE: -0.0802

[2020-12-11 17:56:49,640 INFO] 
SENT 32: ['"@@', '추가', '취업', '희망@@', '자@@', '에다', '구직@@', '단@@', '념@@', '자,', '취업준비@@', '자', '등을', '합친', '청년@@', '층의', '잠재@@', '실업@@', '률은', '23@@', '%에', '달해', '청년', '4명', '가운데', '한', '명이', '실질적인', '실업', '상태에', '놓여', '있는', '상황이다."']
PRED 32: " a f t e r ᴥ n o w , ᴥ r e a l ᴥ h o n o r ᴥ m a y ᴥ b e ᴥ d i g n i n g ᴥ v i c t i m . "
PRED SCORE: -0.0795

[2020-12-11 17:56:49,640 INFO] 
SENT 33: ['지역@@', '산업', '활력', '회복을', '위한', '단기@@', '일자리', '대책이', '포함됐다.']
PRED 33: t h e ᴥ a g e n c y ᴥ w a s ᴥ a ᴥ r e s u l t ᴥ f o r ᴥ r e c o v e r y ᴥ d a y .
PRED SCORE: -0.0816

[2020-12-11 17:56:49,641 INFO] 
SENT 34: ['책임', '부처가', '모호@@', '해지면서', 

[2020-12-11 17:56:50,236 INFO] 
SENT 61: ['이와', '달리', '우@@', '기에는', '목@@', '초가', '무성@@', '해', '구@@', '충@@', '제와', '항생@@', '제의', '수요가', '높다.']
PRED 61: m o r e ᴥ c a m e ᴥ b e ᴥ n o w ᴥ a p p y ᴥ t o ᴥ w a s ᴥ t r u m p .
PRED SCORE: -0.0819

[2020-12-11 17:56:50,236 INFO] 
SENT 62: ['대전@@', '지역', '경제가', '흔들리고', '있다는', '통계가', '지난해부터', '연이어', '나오고', '있다.']
PRED 62: t h e ᴥ w o r d ᴥ s a y s ᴥ t h a t ᴥ t h e ᴥ p r e s s i d e n t ᴥ c o n t i n u e .
PRED SCORE: -0.0815

[2020-12-11 17:56:50,237 INFO] 
SENT 63: ['"남@@', '측에서는', '조용@@', '근', '육군@@', '대@@', '령@@', '과', '관련', '실무@@', '담당@@', '관', '등', '총', '4명@@', '이,', '북@@', '측에서는', '엄@@', '창@@', '남', '육군@@', '대@@', '좌@@', '와', '관련', '실무@@', '담당@@', '관', '등', '총', '4명이', '각각', '참석했다."']
PRED 63: b o y s ᴥ m a y ᴥ h a v e ᴥ s o m e t h i n g ᴥ i n ᴥ t h e ᴥ p r i c e s ᴥ w e r e ᴥ s a l e .
PRED SCORE: -0.0805

[2020-12-11 17:56:50,237 INFO] 
SENT 64: ['다만', '향후', '최저임금', '인상@@', '률이', '높은', '수준을', '유지할', '경우', '커질', '수', '있는', '부작용을', '최소화

[2020-12-11 17:56:50,832 INFO] 
SENT 91: ['"손@@', '석@@', '희', 'JTBC', '대표이사@@', '로부터', '폭행을', '당했다고', '주장하는', '프리랜서', '기자가', '손', '대표를', '협박@@', ',', '명예훼손', '혐의', '등으로', '검찰에', '추가', '고소@@', '했다."']
PRED 91: m a n a g e r ᴥ p o s e d ᴥ n o w ᴥ c o m e ᴥ t o ᴥ p r e p a r e ᴥ i n ᴥ t h e ᴥ w o r k .
PRED SCORE: -0.0819

[2020-12-11 17:56:50,832 INFO] 
SENT 92: ['경찰은', '신도@@', '들의', '휴대전화', '전원을', '끄@@', '도록', '하고', '제출받은', '뒤', '어린이@@', '들을', '포함한', '신도@@', '들의', '개인', '신원을', '일일이', '확인하고', '기록했다.']
PRED 92: t h e ᴥ p o l i c e ᴥ w i l l ᴥ s h o w ᴥ p e o p l e ᴥ a r o u n d ᴥ t h e ᴥ e l d .
PRED SCORE: -0.0823

[2020-12-11 17:56:50,832 INFO] 
SENT 93: ['"@@', '무언@@', '가', '결@@', '심한', '박준@@', '규@@', '는', '초@@', '심을', '찾기', '위한', '극@@', '단의', '조치를', '취@@', '하게', '되는데,', '이로', '인해', '가족@@', '들@@', '간', '분위기가', '싸@@', '해진다."']
PRED 93: t h e n ᴥ i n ᴥ v a i n ᴥ t o ᴥ f i n d ᴥ o r ᴥ g i v e ᴥ a ᴥ d r a m a g e .
PRED SCORE: -0.0808

[2020-12-11 17:56:50,832 INFO] 
SENT 94: ['올해는', '개방형'

[2020-12-11 17:56:50,836 INFO] 
SENT 117: ['"@@', '냉@@', '방', '수요는', '어느', '정도', '한@@', '도가', '있기', '때문에', '저희@@', '들이', '충분히', '그@@', '만한', '예비', '전력이', '있@@', '다,', '라고', '보@@', '시면', '되@@', '겠습니다."']
PRED 117: i ᴥ c o u l d ᴥ b e ᴥ a ᴥ h o p e ᴥ t h a t ᴥ s e n s e ᴥ i s ᴥ a n ᴥ e x p l a c e .
PRED SCORE: -0.0812

[2020-12-11 17:56:50,836 INFO] 
SENT 118: ['"모든', '것을', '하나하나', '자신의', '손으로', '구축@@', '하고자', '하는', '열@@', '의를', '꺾고', '싶은', '것은', '아니지만,', '이는', '상당한', '비용과', '시간이', '투여@@', '된다."']
PRED 118: " n o w ᴥ t o ᴥ d e c i s i o n , ᴥ b u t ᴥ m a k e ᴥ a ᴥ p e r f o r m a n c e . "
PRED SCORE: -0.0825

[2020-12-11 17:56:50,836 INFO] 
SENT 119: ['"@@', '티켓@@', '이', '없어도', '한강@@', '공원에', '펼쳐질', '피크@@', '닉', '공간,', '50@@', '개', '이상의', '플리@@', '마켓@@', '과', '푸드@@', '트럭', '등은', '누구@@', '든지', '즐길', '수', '있다."']
PRED 119: i ᴥ a m ᴥ p l a n n i n g ᴥ t o ᴥ o p e n ᴥ w h e n ᴥ t h e ᴥ d a y ᴥ c o m e .
PRED SCORE: -0.0827

[2020-12-11 17:56:50,836 INFO] 
SENT 120: ['노동자들이', '생명을', '내걸고', 

...

[2020-12-11 17:59:30,852 INFO] 
SENT 7891: ['그중', '하나가', '도시@@', '계획을', '통한', '공동체', '조성과', '공유@@', '가치', '실현@@', '이다.']
PRED 7891: o n e ᴥ o f ᴥ t h e m ᴥ i s ᴥ a ᴥ d e l o c a t e ᴥ f o r ᴥ m y ᴥ c h i l d r e n ᴥ b e g i n .
PRED SCORE: -0.0809

[2020-12-11 17:59:30,852 INFO] 
SENT 7892: ['모든', '멤버가', '10@@', '대로', '구성된', '6@@', '인@@', '조', '그룹', '‘더', '이@@', '스트', '라이트@@', '’', '폭행', '사건의', '철저한', '수사를', '촉구하는', '국민청원', '동의', '수가', '청와대', '답변', '기준인', '20만@@', '명을', '넘어섰다.']
PRED 7892: c h e o n g ᴥ w a ᴥ d a e ᴥ a r e ᴥ i n v e s t i g a t i o n ᴥ u n d e r s t a n d .
PRED SCORE: -0.0819

[2020-12-11 17:59:30,853 INFO] 
SENT 7893: ['점유율', '1위인', '신라@@', '면이', '이', '같은', '변화에', '직격탄을', '맞@@', '았다는', '해석@@', '이다.']
PRED 7893: t h e ᴥ s c h o o l ᴥ b e ᴥ a ᴥ f u n d s ᴥ i s ᴥ t h e ᴥ p r i c e ᴥ w a s ᴥ l e a d i n g .
PRED SCORE: -0.0815

[2020-12-11 17:59:30,853 INFO] 
SENT 7894: ['미국', '경기', '둔화', '조짐@@', '은', '미국', '연방준비@@', '제도의', '금리', '인상', '압력이', '완화@@', '되는', '계기가', '될', '수

[2020-12-11 17:59:31,482 INFO] 
SENT 7921: ['권@@', '용수', '주@@', '우즈베키스탄', '대사는', '“@@', '스마트@@', '미터', '프로젝트의', '성공', '추진을', '바탕으로', 'KT@@', '의', '우즈@@', '벡', '사업이', '다양한', 'ICT', '분야로', '확대@@', '돼', '나가@@', '기를', '바란다”고', '밝혔다.']
PRED 7921: s o m e ᴥ s a y ᴥ t h a t ᴥ c e n t r o l ᴥ k n o w s ᴥ i s ᴥ d e s i r e ᴥ t o ᴥ m a k e .
PRED SCORE: -0.0797

[2020-12-11 17:59:31,482 INFO] 
SENT 7922: ['펑@@', '샨@@', '샨@@', '의', '뒤를', '이@@', '을', '중국', '여자', '골프@@', '의', '미래@@', '로', '불리는', '수@@', '이@@', '샹@@', '은', '특히', '쇼트@@', '게임', '능력이', '뛰@@', '나@@', '다는', '평가를', '받는다.']
PRED 7922: " i n ᴥ t h e ᴥ p r o b l e m , ᴥ t h e ᴥ s o m e ᴥ d i d n ' t ᴥ f e e l ᴥ c h i n a . "
PRED SCORE: -0.0799

[2020-12-11 17:59:31,482 INFO] 
SENT 7923: ['영어가', '정규', '교과@@', '로', '편성@@', '되는', '것은', '초등학교', '3@@', '학년@@', '부터다.']
PRED 7923: i n - s u k ᴥ t h r e e ᴥ g r a n d s h i p ᴥ t o ᴥ l o v e ᴥ a s ᴥ s e c r e t s ᴥ m a r k e t .
PRED SCORE: -0.0807

[2020-12-11 17:59:31,482 INFO] 
SENT 7924: ['"@@', 

[2020-12-11 17:59:32,110 INFO] 
SENT 7951: ['카타@@', '르는', '4@@', '경기@@', '서', '10@@', '골을', '허용@@', '했을', '정도로', '수비가', '약한', '팀@@', '이기', '때문에', '정상적으로', '상대@@', '하면', '충분히', '이길', '수', '있는', '상대@@', '다.']
PRED 7951: b i n g ᴥ h a s ᴥ m o r e ᴥ s t a y s ᴥ w h e n ᴥ t h e ᴥ d o g ᴥ c a n ᴥ w e r e ᴥ g o .
PRED SCORE: -0.0833

[2020-12-11 17:59:32,110 INFO] 
SENT 7952: ['대상@@', '㈜@@', '에서', '제조@@', '한', '청정@@', '원', '‘@@', '런@@', '천@@', '미@@', '트@@', '’의', '일부', '제품에서', '세균이', '검출@@', '돼', '식품의약품안전@@', '처@@', '로부터', '판매', '중단', '및', '회수@@', '조치', '판정을', '받았다.']
PRED 7952: s o m e ᴥ s a y ᴥ t h e ᴥ p r o b l e m ᴥ w i t h ᴥ m o v i e ᴥ c a n ᴥ d e n i n g .
PRED SCORE: -0.0812

[2020-12-11 17:59:32,110 INFO] 
SENT 7953: ['"강@@', '씨', '등은', '김씨가', '휴대전화', '가@@', '개통', '이후', '판매', '대금', '일부를', '가로@@', '챘@@', '다는', '이유로', '아파트', '주차@@', '장과', '공원,', '모@@', '텔', '객@@', '실에서', '5시간', '가까이', '폭행한', '것으로', '드러났다."']
PRED 7953: t h e ᴥ w i n d o w ᴥ o f ᴥ t h e ᴥ p l a n e ᴥ c h a n g e s ᴥ i s

[2020-12-11 17:59:32,726 INFO] 
SENT 7981: ['"@@', '근대@@', '건축물', '기록@@', '보존@@', '사업은', '지난', '2010년부터', '광주시가', '추진하고', '있는', '사업@@', '으로,', '그동안', '사업@@', '대상', '건물@@', '주의', '비@@', '협조@@', '와', '건축물', '산@@', '재로', '사업@@', '추진에', '적지', '않은', '어려움을', '겪@@', '었다."']
PRED 7981: t h e ᴥ f o u r ᴥ b r i n g s ᴥ a r e ᴥ m a s s i n g ᴥ h e r ᴥ l e a d e r ᴥ c h i n a .
PRED SCORE: -0.0823

[2020-12-11 17:59:32,726 INFO] 
SENT 7982: ['보도에', '따르면', '방', '전', '대표', '주변@@', '인들은', '방', '전', '대표가', '장', '씨와', '2008@@', '년@@', '∼@@', '2009@@', '년에', '잠시', '동안', '자주', '만나는', '사이@@', '였으며', '방', '대표가', '장', '씨를', '언급@@', '하기도', '했다고', '진술했다.']
PRED 7982: c h a ᴥ j o o - h y u k ' s ᴥ w e d e n ᴥ i n ᴥ a ᴥ m e d i u m ᴥ w a s ᴥ b u r d e n .
PRED SCORE: -0.0816

[2020-12-11 17:59:32,726 INFO] 
SENT 7983: ['대기', '등록@@', '자만', '200여@@', '명에', '달할', '정도로', '주민들의', '관심이', '높다.']
PRED 7983: a n y ᴥ a f t e r ᴥ t h e ᴥ n e w ᴥ o r d ᴥ c l o s e ᴥ b e f o r e ᴥ g r e a t e r .
PRED SCORE: -0.0810

[2020-

[2020-12-11 17:59:33,198 INFO] 
SENT 8011: ['다만', '북미가', '공동', '유해@@', '발굴', '사업에', '합의@@', '한다면', '미국', '장비@@', '의', '대북', '반입@@', '과', '발굴', '비용', '지@@', '불', '등을', '위한', '대북제재', '예외', '인@@', '정이', '필요하다.']
PRED 8011: p e o p l e ᴥ w e r e ᴥ n o t ᴥ a l l ᴥ t h e ᴥ u n i t e d ᴥ i n ᴥ m y ᴥ c h a n g e .
PRED SCORE: -0.0818

[2020-12-11 17:59:33,198 INFO] 
SENT 8012: ['출산@@', '과', '육아@@', '에', '대한', '부담이', '부모에게', '지나치게', '쏠리는', '환경을', '개선@@', '하지', '않으면', '저출산', '문제를', '해결하는', '건', '요원@@', '하다.']
PRED 8012: i t ᴥ w a s ᴥ h u g e ᴥ t o ᴥ c h i l d c a r e ᴥ c e n t e r s ᴥ w a s ᴥ u s e f u l .
PRED SCORE: -0.0808

[2020-12-11 17:59:33,198 INFO] 
SENT 8013: ['여기', '국내', '론@@', '칭', '이후', '누적@@', '판매', '10만@@', '대를', '돌파한', '유모@@', '차가', '있다.']
PRED 8013: m y ᴥ c o a c h e s ᴥ i s ᴥ t a l k i n g ᴥ t o ᴥ b e ᴥ m o d e l e ᴥ h e a r t .
PRED SCORE: -0.0807

[2020-12-11 17:59:33,198 INFO] 
SENT 8014: ['모두가', '기억하고', '있던', '그의', '통@@', '통한', '모습@@', '과는', '사뭇', '달랐다.']
PRED 8014: e v e r


# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [8]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/morph2bpe/pred.txt

# Post-processing

In [4]:
f = open('OpenNMT-py/Data/tgt-test-char.txt', 'r', encoding='utf-8')
txt = f.read()
txt = txt.replace(' ', '')
txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/tgt-test-char-edited.txt", "w") as f:
    f.write(txt)
    
txt[:1000]

'"according to descriptions by the police, mr. kim, who visited the pc-bang as a guest, had an argument with mr. shin while demanding that food left by other guests be cleared from his seat."\n"as jamsil girls\' high school (principal kim in-bong) is aiming to cultivate talents and good personality, the teachers and students are upgrading their career path programs through the ""team-play of trust""."\nformer lawmaker kim will lose both his right to vote and his right to run for 5 years if a fine of 1 million won or more is confirmed.\n"the working environment of daejeon industrial park in daedeok-gu, daejeon will be improved."\n"around 90t of reinforcement facilities were lost due to high waves at the dongbang breakwater construction site in wimi port, namwon-eup, seogwipo-si, and a 100m median strip fell in the area of nohyeong rotary - samsung service center in jeju."\nit is a program to make students value physical education and art.\n"the us department of justice prosecuted assang

In [17]:
f = open('OpenNMT-py/Data/bpe2char/pred_50k.txt', 'r', encoding='utf-8')
txt = f.read()
txt = txt.replace(' ', '')
txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/bpe2char/pred_50k-edited.txt", "w") as f:
    f.write(txt)

f = open('OpenNMT-py/Data/bpe2char/pred_50k-edited.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'some participate that sense work is alone.\n"in addition, no seoul was more people like this."\na control kim has never desired up.\nthe hold rain leaders for damage in the tourns.\nmy past in the drog and sexpert were for 01920.\nthe sports control much as the prices from korea.\nit may be different should have a continued.\nthe main did not final to be a change the u.s.\ni\'m thinking to take about the followers going.\nnext to has a sprice films led to any chung.\nthe police didn\'t result to be wary of answere.\nthe perfect or white get home is the way.\nthe housing market continues to be share.\nit was the pocial returned for my change in detai.\nthe incident be a character is also next to go.\ni think the area was just come by more.\n"in seenally, the united company is still."\n"it were so many people, but to save and change."\nthe u.s. dictory can be reflection on the shot.\ni think the problems with my in death article.\nthe homemade now days is the flame so respicy.\nsome say

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [18]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test.txt < OpenNMT-py/Data/bpe2char/pred_50k-edited.txt

BLEU = 0.08, 20.9/1.6/0.2/0.0 (BP=0.109, ratio=0.311, hyp_len=70745, ref_len=227303)
